In [1]:
%reload_ext autoreload
%autoreload 2

In [2]:
# default_exp eda

# 赛题说明
https://www.biendata.xyz/competition/chip_2020_1/

本评测任务为面向中文医学文本的命名实体识别，即给定schema及句子sentence，对于给定的一组纯医学文本文档，任务的目标是识别并抽取出与医学临床相关的实体，并将他们归类到预先定义好的类别。将医学文本命名实体划分为九大类，包括：疾病，临床表现，药物，医疗设备，医疗程序，身体，医学检验项目，微生物类，科室。标注之前对文章进行自动分词处理，所有的医学实体均已正确切分。
 
命名实体标注的基本原则：
（1） “临床表现”实体类别中允许嵌套，该实体内部允许存在其他八类实体；
（2） 除了“临床表现”实体之外的医学实体，在标注时遵循“最大单位标注法”，即如果一个实体类别里包含其他的实体，只需要将最大的实体标注出来，不需要做嵌套标注。
（3） 为了保证医学实体意义的可理解性和完整性，九类实体内部可以包含必要的标点符号，实体可以是一个词、短语或句子。
## 赛程


## 数据说明
本次竞赛使用的数据集是由北京大学计算语言学教育部重点实验室、郑州大学信息工程学院自然语言处理实验室、哈尔滨工业大学（深圳）、以及鹏城实验室人工智能研究中心智慧医疗课题组联合构建。总字数达到164万，包含26903个句子，1062个文件，平均每个文件的字数为2393。数据集包含504种常见的儿科疾病、7,085种身体部位、12,907种临床表现、4,354种医疗程序等九大类医学实体。
 
句子记录来源文本，记录医学实体的位置以及标签，医学实体的位置和标签之间以四个空格分隔。该示例中存在临床表现实体中嵌套身体实体。其中“呼吸肌麻痹”、“呼吸中枢受累”为临床表现实体，实体内部分别嵌套“呼吸肌”、“呼吸中枢”身体实体。
 
“呼吸肌麻痹和呼吸中枢受累患者因呼吸不畅可并发肺炎、肺不张等。|||0 2 bod|||0 4 sym|||6 9 bod|||6 11 sym|||15 18 sym|||22 23 dis|||25 27 dis|||”
 
表1中展示实体的标记方案及样例。数据集中的语料来自临床儿科学，数据集划分方式：训练集（22,000），测试集Test1（3,000），测试集Test2(6,618)。
 
其中训练集用于训练，可供自由下载，测试集分为两个，测试集Test1供参赛者在平台上自主验证，测试集Test2在比赛结束前一周发布，不能在平台上自主验证，并将作为最终的评测排名。

## 提交方式

## 评估方式


# 解题思路
## mine

## 大佬


# lib导入

In [2]:
# export
import os
import re
from code.config import args 
from loguru import logger
import numpy as np
import pandas as pd
pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 100)  # 设置显示数据的最大列数，防止出现省略号…，导致数据显示不全
pd.set_option('expand_frame_repr', False)  # 当列太多时不自动换行

from sklearn.metrics import classification_report, accuracy_score
# from mylib.utils.pickle import PickleWrapper

In [3]:
import sys
sys.path.append('..')
import seaborn as sns
sns.set(font='Arial Unicode MS')  # 解决Seaborn中文显示问题
from mylib.data.processing.eda import describe

# EDA

In [12]:
!ls {args.DATA_DIR}

test1.txt  test2.txt  train_data.txt  val_data.txt


# 不考虑嵌套的情况

In [5]:
with open(os.path.join(args.DATA_DIR, 'train_data.txt'), encoding='utf8') as f:
    lines = f.readlines()

with open(os.path.join(args.DATA_DIR, 'val_data.txt'), encoding='utf8') as f:
    lines_val = f.readlines()

with open(os.path.join(args.DATA_DIR, 'test1.txt'), encoding='utf8') as f:
    lines_test = f.readlines()

lines.extend(lines_val)

len(lines), len(lines_val), len(lines_test), lines[:2]

(20000,
 5000,
 3000,
 ['（5）房室结消融和起搏器植入作为反复发作或难治性心房内折返性心动过速的替代疗法。|||3    7    pro|||9    13    pro|||16    33    dis|||\n',
  '（6）发作一次伴血流动力学损害的室性心动过速（ventriculartachycardia），可接受导管消融者。|||8    21    dis|||23    44    dis|||50    53    pro|||\n'])

In [6]:
cls = 'dis sym pro equ dru ite bod dep mic'.split()
for c in cls:
    print(f'B-{c}')
    print(f'I-{c}')

B-dis
I-dis
B-sym
I-sym
B-pro
I-pro
B-equ
I-equ
B-dru
I-dru
B-ite
I-ite
B-bod
I-bod
B-dep
I-dep
B-mic
I-mic


In [7]:
cls_dic = dict()
for c in cls:
    cls_dic[c] = set()

sents = []
marks_list = []
for line in lines:
    ts = line.split('|||')
#     print(ts)
#     print(ts[0])
    sent = ts[0]
    marks = ['O'] * len(sent)
    for i in range(len(ts)):
        if i == 0:
#             print(ts[i])
            pass
        else:
            try:
                start, end, cat = re.split(r'\s+', ts[i])
                cls_dic[cat].add(sent[int(start): (int(end)+1)])
                marks[int(start)] = f'B-{cat}'
                for ii in range((int(start)+1), (int(end)+1)):
                    marks[ii] = f'I-{cat}'
                    
#                 if ts[0][int(start): (int(end)+1)]=='顶':
#                     print(line)
#                     print(start, end, cat)
#                     print(ts[0][int(start): (int(end)+1)], cat)            
            except:
                pass
    sents.append(sent)
    marks_list.append(marks)
#     break

In [9]:
len(sents), len(marks_list)

(20000, 20000)

In [8]:
results = []
for news, marks in zip(sents, marks_list):
    ll = []
    for n, m in zip(news, marks):
        ll.append(f'{n} {m}')
    results.append('\n'.join(ll))

In [9]:
len(results)

20000

In [10]:
with open(os.path.join(args.DATA_GEN, 'train.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[:]))

In [11]:
with open(os.path.join(args.DATA_GEN, 'dev.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[15000:]))

In [12]:
test = []
for i in lines_test:
    test.append('\n'.join(list(i[:-1])))
    
with open(os.path.join(args.DATA_GEN, 'test.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(test))

In [13]:
!python run_ner.py --data_dir {args.DATA_GEN} \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path bert-base-chinese \
--output_dir {args.DATA_GEN}med2 \
--max_seq_length  480 \
--num_train_epochs 3 \
--per_device_train_batch_size 6 \
--save_steps 1000 \
--seed 14 \
--do_train \
--do_eval \
--do_predict

/home/ian/anaconda3/lib/python3.8/site-packages/transformers/training_args.py:289: FutureWarning: The `evaluate_during_training` argument is deprecated in favor of `evaluation_strategy` (which has more options)
  warnings.warn(
09/23/2020 15:16:08 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
09/23/2020 15:16:08 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(output_dir='../../../mydata/data_gen/chip_medner/med2', overwrite_output_dir=False, do_train=True, do_eval=True, do_predict=True, evaluate_during_training=False, evaluation_strategy=<EvaluationStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=6, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=1, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=3.0, max_steps=-

09/23/2020 15:16:24 - INFO - utils_ner -   Writing example 10000 of 20000
09/23/2020 15:16:34 - INFO - utils_ner -   Saving features into cached file ../../../mydata/data_gen/chip_medner/cached_train_BertTokenizer_480
09/23/2020 15:16:40 - INFO - filelock -   Lock 140701447313056 released on ../../../mydata/data_gen/chip_medner/cached_train_BertTokenizer_480.lock
09/23/2020 15:16:40 - INFO - filelock -   Lock 140699639095456 acquired on ../../../mydata/data_gen/chip_medner/cached_dev_BertTokenizer_480.lock
09/23/2020 15:16:40 - INFO - utils_ner -   Creating features from dataset file at ../../../mydata/data_gen/chip_medner/
09/23/2020 15:16:40 - INFO - utils_ner -   Writing example 0 of 5000
09/23/2020 15:16:40 - INFO - utils_ner -   *** Example ***
09/23/2020 15:16:40 - INFO - utils_ner -   guid: dev-1
09/23/2020 15:16:40 - INFO - utils_ner -   tokens: [CLS] 对 儿 童 [UNK] [UNK] [UNK] [UNK] [UNK] 细 胞 亚 群 的 研 究 表 明 ， 与 成 人 [UNK] [UNK] [UNK] [UNK] 相 比 ， 儿 童 细 胞 下 降 不 明 显 ， 证 明 上 述 推 测 成 立 

09/23/2020 15:16:45 - INFO - utils_ner -   Saving features into cached file ../../../mydata/data_gen/chip_medner/cached_dev_BertTokenizer_480
09/23/2020 15:16:46 - INFO - filelock -   Lock 140699639095456 released on ../../../mydata/data_gen/chip_medner/cached_dev_BertTokenizer_480.lock
You are instantiating a Trainer but Tensorboard is not installed. You should consider installing it.
Iteration:   6%|█▋                           | 187/3334 [00:40<11:17,  4.64it/s]


Iteration:  11%|███▎                         | 381/3334 [01:21<10:39,  4.62it/s]


Iteration:  15%|████▎                        | 499/3334 [01:47<10:14,  4.61it/s]{'loss': 0.7056028442382812, 'learning_rate': 4.7500499900019995e-05, 'epoch': 0.14997000599880023, 'total_flos': 883718717760000, 'step': 500}

Iteration:  17%|████▉                        | 573/3334 [02:03<10:07,  4.55it/s]


...

09/23/2020 15:54:48 - INFO - utils_ner -   Saving features into cached file ../../../mydata/data_gen/chip_medner/cached_test_BertTokenizer_480
09/23/2020 15:54:49 - INFO - filelock -   Lock 140698968385424 released on ../../../mydata/data_gen/chip_medner/cached_test_BertTokenizer_480.lock
Prediction: 100%|█████████████████████████████| 375/375 [00:34<00:00, 10.88it/s]
09/23/2020 15:55:54 - INFO - __main__ -     eval_loss = 1.3867758000691732
09/23/2020 15:55:54 - INFO - __main__ -     eval_precision = 0.0
09/23/2020 15:55:54 - INFO - __main__ -     eval_recall = 0
09/23/2020 15:55:54 - INFO - __main__ -     eval_f1 = 0
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'm'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence lengt

09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '：'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'p'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'o'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'T'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'h'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'v'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'l'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'u'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '6'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '，'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '3'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '5'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '4'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '（'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '1'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '）'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '：'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'f'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'c'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'c'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'y'.
09/23/2020 15:55:54 - WARNING - __main__ -   Maximum sequence length exceeded: No 

In [17]:
!python run_ner.py --data_dir {args.DATA_GEN} \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path {args.DATA_GEN}med2 \
--output_dir {args.DATA_GEN}med3 \
--max_seq_length  480 \
--num_train_epochs 2 \
--per_device_train_batch_size 6 \
--save_steps 1000 \
--seed 14 \
--do_train \
--do_eval \
--do_predict

/home/ian/anaconda3/lib/python3.8/site-packages/transformers/training_args.py:289: FutureWarning: The `evaluate_during_training` argument is deprecated in favor of `evaluation_strategy` (which has more options)
  warnings.warn(
09/23/2020 16:03:28 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
09/23/2020 16:03:28 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(output_dir='../../../mydata/data_gen/chip_medner/med3', overwrite_output_dir=False, do_train=True, do_eval=True, do_predict=True, evaluate_during_training=False, evaluation_strategy=<EvaluationStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=6, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=1, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=2.0, max_steps=-

Iteration:  11%|███                          | 357/3334 [01:16<10:44,  4.62it/s]


Iteration:  15%|████▎                        | 499/3334 [01:47<10:16,  4.60it/s]{'loss': 0.2809071044921875, 'learning_rate': 4.6250749850029995e-05, 'epoch': 0.14997000599880023, 'total_flos': 883718717760000, 'step': 500}

Iteration:  16%|████▊                        | 549/3334 [01:58<10:05,  4.60it/s]


Iteration:  22%|██████▍                      | 743/3334 [02:40<09:24,  4.59it/s]


Iteration:  28%|████████▏                    | 937/3334 [03:23<08:42,  4.59it/s]


...

Iteration:  95%|██████████████████████████▌ | 3165/3334 [11:34<00:36,  4.58it/s]{'loss': 0.158279052734375, 'learning_rate': 1.259748050389922e-06, 'epoch': 1.9496100779844032, 'total_flos': 11487165039256320, 'step': 6500}

Iteration:  96%|██████████████████████████▉ | 3202/3334 [11:42<00:28,  4.58it/s]


Epoch: 100%|█████████████████████████████████████| 2/2 [24:21<00:00, 730.78s/it]
/home/ian/anaconda3/lib/python3.8/site-packages/transformers/trainer.py:1108: FutureWarning: This method is deprecated, use `Trainer.is_world_process_zero()` instead.
  warnings.warn("This method is deprecated, use `Trainer.is_world_process_zero()` instead.", FutureWarning)
09/23/2020 16:27:57 - INFO - __main__ -   *** Evaluate ***
Evaluation: 100%|█████████████████████████████| 625/625 [00:58<00:00, 10.72it/s]
{'eval_loss': 0.10665073700472713, 'eval_precision': 0.8172484599589322, 'eval_recall': 0.8979013641133263, 'eval_f1': 0.8556786080347991, 'epoch': 2.0, 'total_flos': 11782916236800000, 'step': 6668}
09/23/2020 16:29:22 - INFO - __main__ -   ***** Eval results *****
09/23/2020 16:29:22 - INFO - __main__ -     eval_loss = 0.10665073700472713
09/23/2020 16:29:22 - INFO - __main__ -     eval_precision = 0.8172484599589322
09/23/2020 16:29:22 - INFO - __main__ -     eval_recall = 0.8979013641133263
09/2

09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'B'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'g'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'U'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '，'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '，'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '1'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '5'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '1'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '（'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '1'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '）'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '：'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '4'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '-'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '1'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '3'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '9'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '6'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '8'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'R'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/23/2020 16:30:29 - WARNING - __main__ -   Maximum sequence length exceeded: No 

## infer

In [18]:
with open(os.path.join(args.DATA_DIR, 'test1.txt'), encoding='utf8') as f:
    lines_test_raw = f.readlines()

# with open('test_predictions.txt', 'r', encoding='utf8') as f:
with open(os.path.join(args.DATA_GEN, 'med3/test_predictions.txt'), 'r', encoding='utf8') as f:
    lines_test = f.readlines()

marks = [line.strip().split()[-1] if line.strip() else '##' for line in lines_test]



marks = ' '.join(marks)

marks = marks.split(' ## ')

print(len(marks))

for i in range(len(lines_test_raw)):
    if i == len(lines_test_raw)-1:
        lines_test_raw[i] =  lines_test_raw[i] + '|||'
    else:
        lines_test_raw[i] =  lines_test_raw[i][:-1] + '|||'
    t = ''
    cat = ''
    marks_i = marks[i].split()
    for ii in range(len(marks_i)):
        if marks_i[ii].startswith('B'):
            cat = marks_i[ii].split('-')[-1]
            t = f'{ii}    '
        elif t and not marks_i[ii].startswith('I'):
            t += f'{ii-1}    {cat}|||'
            lines_test_raw[i] += t
            t = ''
            cat = ''
#     print(lines_test_raw[i])
#     break

3000


In [19]:
with open(os.path.join(args.DATA_GEN, 'med3/test_predictions_sub3.txt'), 'w', encoding='utf8') as f:
    f.write('\n'.join(lines_test_raw))

# 考虑嵌入的情况

## sym

In [20]:
with open(os.path.join(args.DATA_DIR, 'train_data.txt'), encoding='utf8') as f:
    lines = f.readlines()

with open(os.path.join(args.DATA_DIR, 'val_data.txt'), encoding='utf8') as f:
    lines_val = f.readlines()

with open(os.path.join(args.DATA_DIR, 'test1.txt'), encoding='utf8') as f:
    lines_test = f.readlines()

lines.extend(lines_val)

len(lines), len(lines_val), len(lines_test), lines[:2]

(20000,
 5000,
 3000,
 ['（5）房室结消融和起搏器植入作为反复发作或难治性心房内折返性心动过速的替代疗法。|||3    7    pro|||9    13    pro|||16    33    dis|||\n',
  '（6）发作一次伴血流动力学损害的室性心动过速（ventriculartachycardia），可接受导管消融者。|||8    21    dis|||23    44    dis|||50    53    pro|||\n'])

In [21]:
cls = 'dis sym pro equ dru ite bod dep mic'.split()
for c in cls:
    print(f'B-{c}')
    print(f'I-{c}')

B-dis
I-dis
B-sym
I-sym
B-pro
I-pro
B-equ
I-equ
B-dru
I-dru
B-ite
I-ite
B-bod
I-bod
B-dep
I-dep
B-mic
I-mic


In [22]:
cls_dic = dict()
for c in cls:
    cls_dic[c] = set()

sents = []
marks_list = []
for line in lines:
    ts = line.split('|||')
#     print(ts)
#     print(ts[0])
    sent = ts[0]
    marks = ['O'] * len(sent)
    for i in range(len(ts)):
        if i == 0:
#             print(ts[i])
            pass
        else:
            try:
                start, end, cat = re.split(r'\s+', ts[i])
#                 cls_dic[cat].add(sent[int(start): (int(end)+1)])
                if marks[int(start)][-3:] == 'sym': continue
                marks[int(start)] = f'B-{cat}'
                for ii in range((int(start)+1), (int(end)+1)):
                    marks[ii] = f'I-{cat}'
                    
#                 if ts[0][int(start): (int(end)+1)]=='顶':
#                     print(line)
#                     print(start, end, cat)
#                     print(ts[0][int(start): (int(end)+1)], cat)            
            except:
                pass
    sents.append(sent)
    marks_list.append(marks)
#     break

In [23]:
len(sents), len(marks_list)

(20000, 20000)

In [24]:
results = []
for news, marks in zip(sents, marks_list):
    ll = []
    for n, m in zip(news, marks):
        ll.append(f'{n} {m}')
    results.append('\n'.join(ll))

In [25]:
len(results)

20000

In [29]:
!mkdir {os.path.join(args.DATA_GEN, 'sym/')}

In [30]:
with open(os.path.join(args.DATA_GEN, 'sym/train.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[:]))

In [31]:
with open(os.path.join(args.DATA_GEN, 'sym/dev.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[15000:]))

In [32]:
test = []
for i in lines_test:
    test.append('\n'.join(list(i[:-1])))
    
with open(os.path.join(args.DATA_GEN, 'sym/test.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(test))

In [ ]:
!python run_ner.py --data_dir {args.DATA_GEN}sym \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path bert-base-chinese \
--output_dir {args.DATA_GEN}sym_med2 \
--max_seq_length  480 \
--num_train_epochs 3 \
--per_device_train_batch_size 6 \
--save_steps 1000 \
--seed 14 \
--do_train \
--do_eval \
--do_predict

## no sym

In [34]:
with open(os.path.join(args.DATA_DIR, 'train_data.txt'), encoding='utf8') as f:
    lines = f.readlines()

with open(os.path.join(args.DATA_DIR, 'val_data.txt'), encoding='utf8') as f:
    lines_val = f.readlines()

with open(os.path.join(args.DATA_DIR, 'test1.txt'), encoding='utf8') as f:
    lines_test = f.readlines()

lines.extend(lines_val)

len(lines), len(lines_val), len(lines_test), lines[:2]

(20000,
 5000,
 3000,
 ['（5）房室结消融和起搏器植入作为反复发作或难治性心房内折返性心动过速的替代疗法。|||3    7    pro|||9    13    pro|||16    33    dis|||\n',
  '（6）发作一次伴血流动力学损害的室性心动过速（ventriculartachycardia），可接受导管消融者。|||8    21    dis|||23    44    dis|||50    53    pro|||\n'])

In [35]:
cls = 'dis sym pro equ dru ite bod dep mic'.split()
for c in cls:
    print(f'B-{c}')
    print(f'I-{c}')

B-dis
I-dis
B-sym
I-sym
B-pro
I-pro
B-equ
I-equ
B-dru
I-dru
B-ite
I-ite
B-bod
I-bod
B-dep
I-dep
B-mic
I-mic


In [36]:
cls_dic = dict()
for c in cls:
    cls_dic[c] = set()

sents = []
marks_list = []
for line in lines:
    ts = line.split('|||')
#     print(ts)
#     print(ts[0])
    sent = ts[0]
    marks = ['O'] * len(sent)
    for i in range(len(ts)):
        if i == 0:
#             print(ts[i])
            pass
        else:
            try:
                start, end, cat = re.split(r'\s+', ts[i])
#                 cls_dic[cat].add(sent[int(start): (int(end)+1)])
                if cat == 'sym' and marks[int(start)] != 'O': continue
                marks[int(start)] = f'B-{cat}'
                for ii in range((int(start)+1), (int(end)+1)):
                    marks[ii] = f'I-{cat}'
                    
#                 if ts[0][int(start): (int(end)+1)]=='顶':
#                     print(line)
#                     print(start, end, cat)
#                     print(ts[0][int(start): (int(end)+1)], cat)            
            except:
                pass
    sents.append(sent)
    marks_list.append(marks)
#     break

In [37]:
len(sents), len(marks_list)

(20000, 20000)

In [38]:
results = []
for news, marks in zip(sents, marks_list):
    ll = []
    for n, m in zip(news, marks):
        ll.append(f'{n} {m}')
    results.append('\n'.join(ll))

In [39]:
len(results)

20000

In [40]:
!mkdir {os.path.join(args.DATA_GEN, 'nosym/')}

In [41]:
with open(os.path.join(args.DATA_GEN, 'nosym/train.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[:]))

In [42]:
with open(os.path.join(args.DATA_GEN, 'nosym/dev.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(results[15000:]))

In [43]:
test = []
for i in lines_test:
    test.append('\n'.join(list(i[:-1])))
    
with open(os.path.join(args.DATA_GEN, 'nosym/test.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(test))

In [44]:
!python run_ner.py --data_dir {args.DATA_GEN}nosym \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path bert-base-chinese \
--output_dir {args.DATA_GEN}nosym_med2 \
--max_seq_length  480 \
--num_train_epochs 3 \
--per_device_train_batch_size 6 \
--save_steps 1000 \
--seed 14 \
--do_train \
--do_eval \
--do_predict

/home/ian/anaconda3/lib/python3.8/site-packages/transformers/training_args.py:289: FutureWarning: The `evaluate_during_training` argument is deprecated in favor of `evaluation_strategy` (which has more options)
  warnings.warn(
09/23/2020 17:35:51 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
09/23/2020 17:35:51 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(output_dir='../../../mydata/data_gen/chip_medner/nosym_med2', overwrite_output_dir=False, do_train=True, do_eval=True, do_predict=True, evaluate_during_training=False, evaluation_strategy=<EvaluationStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=6, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=1, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=3.0, max_s

09/23/2020 17:36:08 - INFO - utils_ner -   Writing example 10000 of 20000
09/23/2020 17:36:17 - INFO - utils_ner -   Saving features into cached file ../../../mydata/data_gen/chip_medner/nosym/cached_train_BertTokenizer_480
09/23/2020 17:36:23 - INFO - filelock -   Lock 139920646268576 released on ../../../mydata/data_gen/chip_medner/nosym/cached_train_BertTokenizer_480.lock
09/23/2020 17:36:23 - INFO - filelock -   Lock 139918761836704 acquired on ../../../mydata/data_gen/chip_medner/nosym/cached_dev_BertTokenizer_480.lock
09/23/2020 17:36:23 - INFO - utils_ner -   Creating features from dataset file at ../../../mydata/data_gen/chip_medner/nosym
09/23/2020 17:36:23 - INFO - utils_ner -   Writing example 0 of 5000
09/23/2020 17:36:23 - INFO - utils_ner -   *** Example ***
09/23/2020 17:36:23 - INFO - utils_ner -   guid: dev-1
09/23/2020 17:36:23 - INFO - utils_ner -   tokens: [CLS] 对 儿 童 [UNK] [UNK] [UNK] [UNK] [UNK] 细 胞 亚 群 的 研 究 表 明 ， 与 成 人 [UNK] [UNK] [UNK] [UNK] 相 比 ， 儿 童 细 胞 下 降 不

09/23/2020 17:36:23 - INFO - utils_ner -   *** Example ***
09/23/2020 17:36:23 - INFO - utils_ner -   guid: dev-5
09/23/2020 17:36:23 - INFO - utils_ner -   tokens: [CLS] （ 二 ） 临 床 症 状 、 体 征 与 成 年 人 类 似 ， 起 病 急 ， 主 要 表 现 为 发 热 和 咳 嗽 ， 热 峰 高 ， 腋 温 多 在 3 9 ℃ 以 上 ， 发 热 持 续 时 间 平 均 超 过 一 周 。 [SEP]
09/23/2020 17:36:23 - INFO - utils_ner -   input_ids: 101 8020 753 8021 707 2414 4568 4307 510 860 2519 680 2768 2399 782 5102 849 8024 6629 4567 2593 8024 712 6206 6134 4385 711 1355 4178 1469 1495 1644 8024 4178 2292 7770 8024 5573 3946 1914 1762 124 130 360 809 677 8024 1355 4178 2898 5330 3198 7313 2398 1772 6631 6814 671 1453 511 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

Iteration:   9%|██▋                          | 312/3334 [01:07<10:54,  4.62it/s]


Iteration:  15%|████▎                        | 499/3334 [01:47<10:16,  4.60it/s]{'loss': 0.69034716796875, 'learning_rate': 4.7500499900019995e-05, 'epoch': 0.14997000599880023, 'total_flos': 883718717760000, 'step': 500}

Iteration:  15%|████▍                        | 504/3334 [01:48<10:14,  4.60it/s]


...

Iteration:  70%|███████████████████▌        | 2331/3334 [08:30<03:38,  4.58it/s]{'loss': 0.2568984375, 'learning_rate': 5.008998200359928e-06, 'epoch': 2.699460107978404, 'total_flos': 15904580336432640, 'step': 9000}

Iteration:  74%|████████████████████▋       | 2466/3334 [09:01<03:09,  4.58it/s]


Iteration:  80%|██████████████████████▎     | 2660/3334 [09:43<02:27,  4.58it/s]


Iteration:  85%|███████████████████████▊    | 2831/3334 [10:21<01:49,  4.59it/s]{'loss': 0.2501220703125, 'learning_rate': 2.509498100379924e-06, 'epoch': 2.8494301139772045, 'total_flos': 16788299054192640, 'step': 9500}

Iteration:  86%|███████████████████████▉    | 2852/3334 [10:25<01:45,  4.59it/s]


Iteration:  89%|████████████████████████▊   | 2961/3334 [10:49<01:21,  4.58it/s]

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## infer

In [46]:
with open(os.path.join(args.DATA_DIR, 'test1.txt'), encoding='utf8') as f:
    lines_test_raw = f.readlines()

# with open('test_predictions.txt', 'r', encoding='utf8') as f:
with open(os.path.join(args.DATA_GEN, 'sym_med2/test_predictions.txt'), 'r', encoding='utf8') as f:
    lines_test = f.readlines()

marks = [line.strip().split()[-1] if line.strip() else '##' for line in lines_test]



marks = ' '.join(marks)

marks = marks.split(' ## ')

print(len(marks))

3000


In [48]:
with open(os.path.join(args.DATA_GEN, 'nosym_med2/test_predictions.txt'), 'r', encoding='utf8') as f:
    lines_test = f.readlines()

marks_nosym = [line.strip().split()[-1] if line.strip() else '##' for line in lines_test]



marks_nosym = ' '.join(marks_nosym)

marks_nosym = marks_nosym.split(' ## ')

print(len(marks_nosym))

3000


In [47]:
marks[:2]

['O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O B-pro O O I-pro I-pro O I-pro O O O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O',
 'O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O O O O O O O O B-dis O I-dis I-dis I-dis I-dis I-dis I-dis O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O B-pro I-pro I-pro I-pro I-pro O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O B-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro O O B-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O O O O']

In [49]:
marks_nosym[:2]

['O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O B-dis I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O',
 'O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O O O O O O O O B-dis O O I-dis O I-dis I-dis O O O O O O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O B-pro I-pro I-pro I-pro I-pro O B-pro I-pro I-pro I-pro I-pro I-pro I-pro O B-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro O O B-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O O O O O O O O O']

In [50]:
for i in range(len(lines_test_raw)):
    if i == len(lines_test_raw)-1:
        lines_test_raw[i] =  lines_test_raw[i] + '|||'
    else:
        lines_test_raw[i] =  lines_test_raw[i][:-1] + '|||'
    t = ''
    cat = ''
    marks_i = marks[i].split()
    marks_nosym_i = marks_nosym[i].split()
    for ii in range(len(marks_nosym_i)):
        if marks_nosym_i[ii].startswith('B'):
            cat = marks_nosym_i[ii].split('-')[-1]
            if cat == 'sym': continue
            t = f'{ii}    '
        elif t and not marks_nosym_i[ii].startswith('I'):
            t += f'{ii-1}    {cat}|||'
            lines_test_raw[i] += t
            t = ''
            cat = ''
    for ii in range(len(marks_i)):
        if marks_i[ii].startswith('B'):
            cat = marks_i[ii].split('-')[-1]
            if cat != 'sym': continue
            t = f'{ii}    '
        elif t and not marks_i[ii].startswith('I'):
            t += f'{ii-1}    {cat}|||'
            lines_test_raw[i] += t
            t = ''
            cat = ''
#     print(lines_test_raw[i])
#     break

In [51]:
lines_test_raw[0]

'六、新生儿疾病筛查的发展趋势自1961年开展苯丙酮尿症筛查以来，随着医学技术的发展，符合进行新生儿疾病筛查标准的疾病也在不断增加，无论在新生儿疾病筛查的病种，还是在新生儿疾病筛查的技术方法上，都有了非常显著的进步。|||2    8    pro|||22    28    dis|||46    52    pro|||68    74    pro|||82    88    pro|||'

In [52]:
with open(os.path.join(args.DATA_GEN, 'test_predictions_combine.txt'), 'w', encoding='utf8') as f:
    f.write('\n'.join(lines_test_raw))

## b榜提交

In [30]:
with open(os.path.join(args.DATA_DIR, 'test2.txt'), encoding='utf8') as f:
    lines_test2 = f.readlines()

In [31]:
test = []
for i in lines_test2:
    test.append('\n'.join(list(i[:-1])))
    
with open(os.path.join(args.DATA_GEN, 'test2.txt'), 'w', encoding='utf8') as f:
    f.write('\n\n'.join(test))

In [39]:
!python run_ner.py --data_dir {args.DATA_GEN}sym \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path {args.DATA_GEN}sym_med2 \
--output_dir {args.DATA_GEN}sym_med_final \
--max_seq_length  480 \
--per_device_train_batch_size 6 \
--do_predict

/home/ian/anaconda3/lib/python3.8/site-packages/transformers/training_args.py:289: FutureWarning: The `evaluate_during_training` argument is deprecated in favor of `evaluation_strategy` (which has more options)
  warnings.warn(
09/29/2020 10:02:00 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
09/29/2020 10:02:00 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(output_dir='../../../mydata/data_gen/chip_medner/sym_med_final', overwrite_output_dir=False, do_train=False, do_eval=False, do_predict=True, evaluate_during_training=False, evaluation_strategy=<EvaluationStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=6, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=1, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=3.0, 

09/29/2020 10:02:10 - INFO - utils_ner -   Saving features into cached file ../../../mydata/data_gen/chip_medner/sym/cached_test_BertTokenizer_480
09/29/2020 10:02:11 - INFO - filelock -   Lock 140649960378912 released on ../../../mydata/data_gen/chip_medner/sym/cached_test_BertTokenizer_480.lock
Prediction: 100%|█████████████████████████████| 703/703 [01:04<00:00, 10.93it/s]
/home/ian/anaconda3/lib/python3.8/site-packages/transformers/trainer.py:1108: FutureWarning: This method is deprecated, use `Trainer.is_world_process_zero()` instead.
  warnings.warn("This method is deprecated, use `Trainer.is_world_process_zero()` instead.", FutureWarning)
09/29/2020 10:04:14 - INFO - __main__ -     eval_loss = 1.2982251867147985
09/29/2020 10:04:14 - INFO - __main__ -     eval_precision = 0.0
09/29/2020 10:04:14 - INFO - __main__ -     eval_recall = 0
09/29/2020 10:04:14 - INFO - __main__ -     eval_f1 = 0
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No predicti

09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'o'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 's'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'F'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'u'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'c'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'c'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'E'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'D'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '2'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '3'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '6'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '陈'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '凌'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '，'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '张'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '建'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'c'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 's'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'h'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'u'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 's'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'l'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'h'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 's'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/29/2020 10:04:14 - WARNING - __main__ -   Maximum sequence length exceeded: No 

In [40]:
!python run_ner.py --data_dir {args.DATA_GEN}sym \
--labels {args.DATA_GEN}labels.txt \
--model_name_or_path {args.DATA_GEN}nosym_med2 \
--output_dir {args.DATA_GEN}nosym_med_final \
--max_seq_length  480 \
--per_device_train_batch_size 6 \
--do_predict

/home/ian/anaconda3/lib/python3.8/site-packages/transformers/training_args.py:289: FutureWarning: The `evaluate_during_training` argument is deprecated in favor of `evaluation_strategy` (which has more options)
  warnings.warn(
09/29/2020 10:04:15 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: False
09/29/2020 10:04:15 - INFO - __main__ -   Training/evaluation parameters TrainingArguments(output_dir='../../../mydata/data_gen/chip_medner/nosym_med_final', overwrite_output_dir=False, do_train=False, do_eval=False, do_predict=True, evaluate_during_training=False, evaluation_strategy=<EvaluationStrategy.NO: 'no'>, prediction_loss_only=False, per_device_train_batch_size=6, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=1, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=3.0

09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '7'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '朱'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '子'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '扬'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '.'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '中'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '毒'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '急'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'n'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'a'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'o'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'g'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'v'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'i'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'e'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'w'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '：'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'u'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'A'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'r'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'h'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'y'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 't'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'h'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'm'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'o'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No 

09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '，'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '9'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '2'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for '（'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 's'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'u'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'p'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'p'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No prediction for 'l'.
09/29/2020 10:06:22 - WARNING - __main__ -   Maximum sequence length exceeded: No 

In [41]:
with open(os.path.join(args.DATA_DIR, 'test2.txt'), encoding='utf8') as f:
    lines_test_raw = f.readlines()

# with open('test_predictions.txt', 'r', encoding='utf8') as f:
with open(os.path.join(args.DATA_GEN, 'sym_med_final/test_predictions.txt'), 'r', encoding='utf8') as f:
    lines_test = f.readlines()

marks = [line.strip().split()[-1] if line.strip() else '##' for line in lines_test]



marks = ' '.join(marks)

marks = marks.split(' ## ')

print(len(marks))

5618


In [42]:
with open(os.path.join(args.DATA_GEN, 'nosym_med_final/test_predictions.txt'), 'r', encoding='utf8') as f:
    lines_test = f.readlines()

marks_nosym = [line.strip().split()[-1] if line.strip() else '##' for line in lines_test]



marks_nosym = ' '.join(marks_nosym)

marks_nosym = marks_nosym.split(' ## ')

print(len(marks_nosym))

5618


In [43]:
marks[:2]

['O O B-equ I-equ I-equ I-equ I-equ I-equ O O O O O O O O O O O B-pro I-pro I-pro I-pro O O O O O O',
 'O O B-pro O B-pro I-pro O B-pro I-pro I-pro I-pro I-pro I-dru I-dru I-pro I-pro I-pro I-pro O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O']

In [44]:
marks_nosym[:2]

['O O B-equ I-equ I-equ I-equ I-equ I-equ O O O O O O O O O O O B-pro I-pro I-pro I-pro O O O O O O',
 'O O B-pro O I-pro I-pro O B-pro I-pro I-pro B-dru I-dru I-dru I-dru B-pro I-pro I-pro I-pro O O O B-pro I-pro I-pro I-pro I-pro I-pro I-pro I-pro O O O O O O O O O O O O O O']

In [45]:
len(lines_test_raw)

5618

In [46]:
for i in range(len(lines_test_raw)):
    if i == len(lines_test_raw)-1:
        lines_test_raw[i] =  lines_test_raw[i] + '|||'
    else:
        lines_test_raw[i] =  lines_test_raw[i][:-1] + '|||'
    t = ''
    cat = ''
    try:
        marks_i = marks[i].split()
        marks_nosym_i = marks_nosym[i].split()
        for ii in range(len(marks_nosym_i)):
            if marks_nosym_i[ii].startswith('B'):
                cat = marks_nosym_i[ii].split('-')[-1]
                if cat == 'sym': continue
                t = f'{ii}    '
            elif t and not marks_nosym_i[ii].startswith('I'):
                t += f'{ii-1}    {cat}|||'
                lines_test_raw[i] += t
                t = ''
                cat = ''
        for ii in range(len(marks_i)):
            if marks_i[ii].startswith('B'):
                cat = marks_i[ii].split('-')[-1]
                if cat != 'sym': continue
                t = f'{ii}    '
            elif t and not marks_i[ii].startswith('I'):
                t += f'{ii-1}    {cat}|||'
                lines_test_raw[i] += t
                t = ''
                cat = ''
    except Exception as e:
        print(e, i)
#     print(lines_test_raw[i])
#     break

In [37]:
lines_test_raw[0]

'由于纤维支气管镜结构细软，多数患儿能在局部麻醉下接受检查。|||2    8    pro|||22    -1    dis|||'

In [47]:
lines_test_raw[0]

'由于纤维支气管镜结构细软，多数患儿能在局部麻醉下接受检查。|||2    7    equ|||19    22    pro|||'

In [48]:
with open(os.path.join(args.DATA_GEN, 'test_predictions_combine_final.txt'), 'w', encoding='utf8') as f:
    f.write('\n'.join(lines_test_raw))